# **\[SOLAR\]** GConvGRU

JiyunLim  
2023-07-20

In [2]:
%run 0720.py

In [3]:
import itertools
import time

In [4]:
# read dataframe 
df = pd.read_csv('data_eng_230710.csv')

# make y, y_upper, y_period, time, regions 
y = df.loc[:,'Bukchoncheon':'Gyeongju-si'].to_numpy()
yU = df.loc[:,'Bukchoncheon_Upper':'Gyeongju-si_Upper'].to_numpy()
yP = np.divide(y, yU+1e-10)
t = df.loc[:,'date']
regions = list(df.loc[:,'Bukchoncheon':'Gyeongju-si'].columns)

TRAIN_RATIO = 0.8
T,N = len(t),len(regions) 
LEN_TEST = int(np.floor(T*(1-TRAIN_RATIO)))
LEN_TR = T - LEN_TEST

In [5]:
import datetime

# GConvGRU

## `-` lag=4

In [ ]:
method = ['classic','proposed']
lags = [4]
filters = [4, 8, 16, 32] 
epoch = [10, 30]

# model_name = 'RecurrentGCN' ### 모델변경시 수정필요
model_name = 'GConvGRU'

col = ['model', 'method', 'lags', 
       'nof_filters', 'epoch', 'calculation_time',
       'index_time',
       'node', 'mse']
df = pd.DataFrame(columns=col)


for iteration in range(50):
    for m,l,f,e in itertools.product(method, lags, filters, epoch):
        if m == 'classic':
            t1 = time.time()
            model = RecurrentGCN(node_features=l, filters=f) ### 모델변경시 수정필요
            yhat = rgcn(y, model = model, train_ratio = TRAIN_RATIO, lags=l, epoch=e)
            yhat[yhat < 0]= 0   
            t2 = time.time()
            c = t2-t1
            t = str(datetime.datetime.now())
            _df2 = pd.concat([pd.Series(regions),pd.Series(((y - yhat)[LEN_TR:, :] ** 2).mean(axis=0))],axis=1)
            _df1 = pd.DataFrame([[model_name,m,l,f,e,c,t]]*N)
            _df = pd.concat([_df1,_df2],axis=1).set_axis(col,axis=1)
            df = pd.concat([df,_df])
        else: # proposed 
            t1 = time.time()
            model = RecurrentGCN(node_features=l, filters=f) ### 모델변경시 수정필요
            yUhat = rgcn(yU, model = model, train_ratio = 0.8, lags=l, epoch=e)
            model = RecurrentGCN(node_features=l, filters=f) ### 모델변경시 수정필요
            yPhat = rgcn(yP, model = model, train_ratio = 0.8, lags=l, epoch=e)
            yPhat[yPhat < 0] =0 
            yhat = yUhat*yPhat
            t2 = time.time()
            c = t2-t1
            t = str(datetime.datetime.now())
            _df2 = pd.concat([pd.Series(regions),pd.Series(((y - yhat)[LEN_TR:, :] ** 2).mean(axis=0))],axis=1)
            _df1 = pd.DataFrame([[model_name,m,l,f,e,c,t]]*N)
            _df = pd.concat([_df1,_df2],axis=1).set_axis(col,axis=1)
            df = pd.concat([df,_df])

5/300

In [54]:
# path = './RLST/GConvGRU/'
# df.to_csv(path+'GConvGRU_LAG4.csv', index=False)

In [119]:
df_summary = df.groupby(by=['method', 'nof_filters', 'epoch']).agg({'mse':[np.mean, np.std]}).reset_index()
df_summary[df_summary['epoch']==10]

In [120]:
df_summary[df_summary['epoch']==30]

### note

-   특정 지역이 안좋게 나오는지 확인

## `-` lag=8

In [6]:
method = ['classic','proposed']
lags = [8]
# filters = [4, 8, 16, 32] 
# epoch = [10, 30] 
filters = [4]
epoch = [30]

# model_name = 'RecurrentGCN' ### 모델변경시 수정필요
model_name = 'GConvGRU'

col = ['model', 'method', 'lags', 
       'nof_filters', 'epoch', 'calculation_time',
       'index_time',
       'node', 'mse']
df_lag8 = pd.DataFrame(columns=col)


for iteration in range(1):
    for m,l,f,e in itertools.product(method, lags, filters, epoch):
        if m == 'classic':
            t1 = time.time()
            model = RecurrentGCN(node_features=l, filters=f) ### 모델변경시 수정필요
            yhat = rgcn(y, model = model, train_ratio = TRAIN_RATIO, lags=l, epoch=e)
            yhat[yhat < 0]= 0   
            t2 = time.time()
            c = t2-t1
            t = str(datetime.datetime.now())
            _df2 = pd.concat([pd.Series(regions),pd.Series(((y - yhat)[LEN_TR:, :] ** 2).mean(axis=0))],axis=1)
            _df1 = pd.DataFrame([[model_name,m,l,f,e,c,t]]*N)
            _df = pd.concat([_df1,_df2],axis=1).set_axis(col,axis=1)
            df_lag8 = pd.concat([df_lag8,_df])
        else: # proposed 
            t1 = time.time()
            model = RecurrentGCN(node_features=l, filters=f) ### 모델변경시 수정필요
            yUhat = rgcn(yU, model = model, train_ratio = 0.8, lags=l, epoch=e)
            model = RecurrentGCN(node_features=l, filters=f) ### 모델변경시 수정필요
            yPhat = rgcn(yP, model = model, train_ratio = 0.8, lags=l, epoch=e)
            yPhat[yPhat < 0] =0 
            yhat = yUhat*yPhat
            t2 = time.time()
            c = t2-t1
            t = str(datetime.datetime.now())
            _df2 = pd.concat([pd.Series(regions),pd.Series(((y - yhat)[LEN_TR:, :] ** 2).mean(axis=0))],axis=1)
            _df1 = pd.DataFrame([[model_name,m,l,f,e,c,t]]*N)
            _df = pd.concat([_df1,_df2],axis=1).set_axis(col,axis=1)
            df_lag8 = pd.concat([df_lag8,_df])

30/30

In [12]:
df_summary2 = df_lag8.groupby(by=['method']).agg({'mse':[np.mean, np.std]})
df_summary2

In [ ]:
# path = './RLST/GConvGRU/'
# df_lag8.to_csv(path+'GConvGRU_LAG8.csv', index=False)

## `-` lag=12

In [14]:
method = ['classic','proposed']
lags = [12, 24]
# filters = [4, 8, 16, 32] 
# epoch = [10, 30] 
filters = [4]
epoch = [30]

# model_name = 'RecurrentGCN' ### 모델변경시 수정필요
model_name = 'GConvGRU'

col = ['model', 'method', 'lags', 
       'nof_filters', 'epoch', 'calculation_time',
       'index_time',
       'node', 'mse']
df_lag12 = pd.DataFrame(columns=col)


for iteration in range(1):
    for m,l,f,e in itertools.product(method, lags, filters, epoch):
        if m == 'classic':
            t1 = time.time()
            model = RecurrentGCN(node_features=l, filters=f) ### 모델변경시 수정필요
            yhat = rgcn(y, model = model, train_ratio = TRAIN_RATIO, lags=l, epoch=e)
            yhat[yhat < 0]= 0   
            t2 = time.time()
            c = t2-t1
            t = str(datetime.datetime.now())
            _df2 = pd.concat([pd.Series(regions),pd.Series(((y - yhat)[LEN_TR:, :] ** 2).mean(axis=0))],axis=1)
            _df1 = pd.DataFrame([[model_name,m,l,f,e,c,t]]*N)
            _df = pd.concat([_df1,_df2],axis=1).set_axis(col,axis=1)
            df_lag12 = pd.concat([df_lag12,_df])
        else: # proposed 
            t1 = time.time()
            model = RecurrentGCN(node_features=l, filters=f) ### 모델변경시 수정필요
            yUhat = rgcn(yU, model = model, train_ratio = 0.8, lags=l, epoch=e)
            model = RecurrentGCN(node_features=l, filters=f) ### 모델변경시 수정필요
            yPhat = rgcn(yP, model = model, train_ratio = 0.8, lags=l, epoch=e)
            yPhat[yPhat < 0] =0 
            yhat = yUhat*yPhat
            t2 = time.time()
            c = t2-t1
            t = str(datetime.datetime.now())
            _df2 = pd.concat([pd.Series(regions),pd.Series(((y - yhat)[LEN_TR:, :] ** 2).mean(axis=0))],axis=1)
            _df1 = pd.DataFrame([[model_name,m,l,f,e,c,t]]*N)
            _df = pd.concat([_df1,_df2],axis=1).set_axis(col,axis=1)
            df_lag12 = pd.concat([df_lag12,_df])

30/30

In [ ]:
# df.to_csv(path+'GConvGRU_LAG12.csv', index=False)

In [16]:
df_summary3 = df_lag12.groupby(by=['method','lags']).agg({'mse':[np.mean, np.std]})
df_summary3

## `-` lag=24

In [ ]:
method = ['classic','proposed']
lags = [24]
filters = [4, 8, 16, 32] 
epoch = [10, 30] 

# model_name = 'RecurrentGCN' ### 모델변경시 수정필요
model_name = 'GConvGRU'

col = ['model', 'method', 'lags', 
       'nof_filters', 'epoch', 'calculation_time',
       'index_time',
       'node', 'mse']
df_lag24 = pd.DataFrame(columns=col)


for iteration in range(50):
    for m,l,f,e in itertools.product(method, lags, filters, epoch):
        if m == 'classic':
            t1 = time.time()
            model = RecurrentGCN(node_features=l, filters=f) ### 모델변경시 수정필요
            yhat = rgcn(y, model = model, train_ratio = TRAIN_RATIO, lags=l, epoch=e)
            yhat[yhat < 0]= 0   
            t2 = time.time()
            c = t2-t1
            t = str(datetime.datetime.now())
            _df2 = pd.concat([pd.Series(regions),pd.Series(((y - yhat)[LEN_TR:, :] ** 2).mean(axis=0))],axis=1)
            _df1 = pd.DataFrame([[model_name,m,l,f,e,c,t]]*N)
            _df = pd.concat([_df1,_df2],axis=1).set_axis(col,axis=1)
            df_lag24 = pd.concat([df_lag24,_df])
        else: # proposed 
            t1 = time.time()
            model = RecurrentGCN(node_features=l, filters=f) ### 모델변경시 수정필요
            yUhat = rgcn(yU, model = model, train_ratio = 0.8, lags=l, epoch=e)
            model = RecurrentGCN(node_features=l, filters=f) ### 모델변경시 수정필요
            yPhat = rgcn(yP, model = model, train_ratio = 0.8, lags=l, epoch=e)
            yPhat[yPhat < 0] =0 
            yhat = yUhat*yPhat
            t2 = time.time()
            c = t2-t1
            t = str(datetime.datetime.now())
            _df2 = pd.concat([pd.Series(regions),pd.Series(((y - yhat)[LEN_TR:, :] ** 2).mean(axis=0))],axis=1)
            _df1 = pd.DataFrame([[model_name,m,l,f,e,c,t]]*N)
            _df = pd.concat([_df1,_df2],axis=1).set_axis(col,axis=1)
            df_lag24 = pd.concat([df_lag24,_df])